# Appendix C: Demonstration of the Intersection-based Spatial Annotation procedure

Import packages and general settings:

In [1]:
import os
import sys

module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)
    
from step import preprocessing as pp
from step import osm

import math
import re
import numpy as np

import gpxpy
import folium
from rdflib import URIRef, Namespace, Graph
import shapely
from shapely import wkt
from shapely.ops import polygonize_full, cascaded_union
import geojson

import matplotlib
import matplotlib.pyplot as plt
import seaborn as sns

%load_ext autoreload
%autoreload 2
%matplotlib inline

matplotlib.rcParams['axes.labelsize'] = 'large'
matplotlib.rcParams['ytick.labelsize'] = 'medium'
matplotlib.rcParams['xtick.labelsize'] = 'medium'
matplotlib.rcParams['legend.edgecolor'] = 'k'
matplotlib.rcParams['legend.shadow'] = True
matplotlib.rcParams['figure.figsize'] = (5, 4)
sns.set_style('ticks', {"axes.xmargin": 0.2, "axes.ymargin": 0.2});

# For pretty printing
import warnings
warnings.simplefilter('ignore')

Load one trajectory file in GPX format:

In [2]:
file_path = r'gpx/49996348-1079694145.gpx'
gpx = gpxpy.parse(open(file_path, 'r'))

In [3]:
points_data = gpx.get_points_data()
points = [(pdata.point.latitude, pdata.point.longitude) for pdata in points_data]

In [4]:
tileset = r'http://{s}.tile.openstreetmap.se/hydda/full/{z}/{x}/{y}.png'
attribution = 'Tiles courtesy of <a href="http://openstreetmap.se/" target="_blank">OpenStreetMap Sweden</a> \
                &mdash; Map data &copy; <a href="http://www.openstreetmap.org/copyright">OpenStreetMap</a>'

_map = folium.Map(tiles=tileset, attr=attribution, max_zoom=25)

start_mark = folium.Marker([points[0][0], points[0][1]], icon=folium.Icon(color='green', icon='glyphicon glyphicon-play'))
start_mark.add_to(_map)

end_mark = folium.Marker([points[-1][0], points[-1][1]], icon=folium.Icon(color='red', icon='glyphicon glyphicon-stop'))
end_mark.add_to(_map)

line = folium.PolyLine(points, opacity=0.8)
line.add_to(_map)
_map.fit_bounds(line.get_bounds())

_map

## Parameters

- `buffer_size` defines the area to be created around each polygon retrieved from OSM

- `minimum_length_ratio` defines the minimum spatial intersection between trajectory and polygon to be considered as relevant

- `minimum_duration_ratio` defines the minimum temporal intersection between trajectory and polygon to be considered as relevant

- `keys` defines which OSM keys are of interest for retrieving OSM features, an empty array means that all keys should be returned

- `expand_keys` sets whether the keys (if not empty) should be expanded according to the related keys found by OSN

In [5]:
buffer_size = 0.0002 # ~20 meters
minimum_length_ratio = 0.2 #delta_s
minimum_duration_ratio = 0.2 #delta_t

keys = ["leisure"]
expand_keys = True

In [6]:
excluded_keys = ['name', 'comment', 'source', 'boundary']
expanded_keys = []

Load Open Semantic Network (OSN) and LinkedGeoData Ontology (LGDO) graphs:

In [7]:
# Search for tags in OSN
if 'osn_graph' not in locals():
    osn_graph = Graph()
    osn_graph.parse('osm_semantic_network.skos.rdf')

if 'lgdo_graph' not in locals():
    lgdo_graph = Graph()
    lgdo_graph.parse('lgdo_2014-07-26.n3', format='n3')

http://spatial.ucd.ie/lod/osn/term/k:source/v:tiger_import_#{date}n does not look like a valid URI, trying to serialize this will break.
http://spatial.ucd.ie/lod/osn/term/k:source/v:tiger_import_#{date}n does not look like a valid URI, trying to serialize this will break.
http://spatial.ucd.ie/lod/osn/term/k:source/v:tiger_import_#{date}n does not look like a valid URI, trying to serialize this will break.
http://spatial.ucd.ie/lod/osn/term/k:source/v:tiger_import_#{date}n does not look like a valid URI, trying to serialize this will break.
http://spatial.ucd.ie/lod/osn/term/k:source/v:tiger_import_#{date}n does not look like a valid URI, trying to serialize this will break.
http://spatial.ucd.ie/lod/osn/term/k:source/v:tiger_import_#{date}n does not look like a valid URI, trying to serialize this will break.
http://spatial.ucd.ie/lod/osn/term/k:source/v:tiger_import_#{date}n does not look like a valid URI, trying to serialize this will break.
http://spatial.ucd.ie/lod/osn/term/k:sour

Using LinkedGeoData to expand keys:

In [8]:
if expand_keys and len(keys) > 0:
    expanded_keys = []
    keys_regex = "|".join(keys)
    regex = r'"http://spatial.ucd.ie/lod/osn/term/k:({0}).*"'.format(keys_regex)
    
    query = """
    PREFIX skos:<http://www.w3.org/2004/02/skos/core#>
    PREFIX rdf:<http://www.w3.org/1999/02/22-rdf-syntax-ns#>
    PREFIX rdfs:<http://www.w3.org/2000/01/rdf-schema#>
    PREFIX xsd:<http://www.w3.org/2001/XMLSchema#>

    SELECT ?subject ?relatedTerm ?lgdConcept
    {
     ?subject skos:related ?relatedTerm .
     ?relatedTerm skos:exactMatch ?lgdConcept .
     
     FILTER (REGEX(STR(?subject), """ + regex +"""))
     FILTER (STRSTARTS(STR(?lgdConcept), "http://linkedgeodata.org/ontology"))
    }"""

    print(query)

    response = osn_graph.query(query)

    for row in response:
        uri = row[1]
        new_key = uri.split('k:')
        if len(new_key) > 1:
            new_key = new_key[-1]
        else:
            continue
        
        try:
            new_key = new_key.split('/')[0]
        except:
            pass
        
        if new_key not in keys:
            expanded_keys.append(new_key)

    expanded_keys = list(set(expanded_keys))

    print()
    print('Input keys: {0}'.format(keys))
    print('{0} new terms found in OSN: {1}'.format(len(expanded_keys), expanded_keys))


    PREFIX skos:<http://www.w3.org/2004/02/skos/core#>
    PREFIX rdf:<http://www.w3.org/1999/02/22-rdf-syntax-ns#>
    PREFIX rdfs:<http://www.w3.org/2000/01/rdf-schema#>
    PREFIX xsd:<http://www.w3.org/2001/XMLSchema#>

    SELECT ?subject ?relatedTerm ?lgdConcept
    {
     ?subject skos:related ?relatedTerm .
     ?relatedTerm skos:exactMatch ?lgdConcept .
     
     FILTER (REGEX(STR(?subject), "http://spatial.ucd.ie/lod/osn/term/k:(leisure).*"))
     FILTER (STRSTARTS(STR(?lgdConcept), "http://linkedgeodata.org/ontology"))
    }

Input keys: ['leisure']
17 new terms found in OSN: ['tourism', 'man_made', 'natural', 'boundary', 'route', 'shelter', 'barrier', 'building', 'sport', 'waterway', 'landuse', 'fishing', 'shop', 'amenity', 'playground', 'harbour', 'highway']


Simplify trajectory's shape and create a WKT representation of it:

In [9]:
gpx_simple = gpx.clone()
gpx_simple.simplify()

linestring_simple = "LINESTRING("

simple_points = gpx_simple.get_points_data()

for i, point_data in enumerate(simple_points):
    point = point_data.point
    linestring_simple += str(point.longitude) + " " + str(point.latitude)
    if i < len(simple_points)-1:
        linestring_simple += ", "

linestring_simple += ")"
linestring_simple

'LINESTRING(5.73425791 45.18210998, 5.735235225 45.1823674714, 5.7407547183 45.1846534569, 5.7429304089 45.1860455704, 5.742455759 45.1867867431, 5.7424284553 45.187952129, 5.7429561659 45.1890001696, 5.74367138 45.1889849224, 5.7451961052 45.1884058183, 5.7478446699 45.1883522866, 5.7494157359 45.1884815264, 5.7505612736 45.1889204948, 5.7495635222 45.1885502523, 5.7470312762 45.1884664258, 5.7454857658 45.1886651283, 5.7439751935 45.189106106, 5.7430106295 45.1889756432, 5.7426115612 45.1884896534, 5.7425259899 45.187664964, 5.742229581 45.1873207084, 5.7426253664 45.186550021, 5.7426946766 45.1858511243, 5.7422678227 45.1855394129)'

### Using Overpass to retrieve OSM features:

In [10]:
all_keys = keys + expanded_keys

osm_features = osm.get_spatial_features(gpx, all_keys)

In [11]:
print('{0} features retrieved.'.format(len(osm_features)))
#first 5 features:
osm_features.head()

124 features retrieved.


geometry  \
id                                                          
80348   MULTILINESTRING((5.7154067 45.1997808,5.715250...   
80349   MULTILINESTRING((5.7430295 45.1663750,5.743081...   
278498  MULTILINESTRING((5.6234964 45.2679788,5.623618...   
558483  MULTILINESTRING((5.7428003 45.1917672,5.742812...   
558491  MULTILINESTRING((5.7491122 45.1888764,5.748643...   

                             label relation  \
id                                            
80348                     Grenoble     None   
80349         Saint-Martin-d'Hères     None   
278498                     L'Isère     None   
558483              Pont du Sablon     None   
558491  Pont de la Porte de Savoie     None   

                                                     tags  
id                                                         
80348   {'addr:postcode': '38000;38100', 'admin_level'...  
80349   {'addr:postcode': '38400', 'admin_level': '8',...  
278498  {'boat': 'no', 'comment': 'Provenance du cadas...  
558483  {'maxweight': '20', 'name': 'Pont du Sablon', ...  
558491  {'name': 'Pont de la Porte de Savoie', 'type':...

Cleaning the dataset to remove OSM features that do not have a tags with corresponding concepts in LGDO:

In [12]:
osn_terms = []
invalid_chars = [' ', '<', '>', '|']

for tags in osm_features['tags']:
        for item in tags.items():
            if item[0] not in excluded_keys and re.match('[a-z]*', item[0]) and re.match('[a-z]*', item[1]):
                uri = "http://spatial.ucd.ie/lod/osn/term/k:{0}/v:{1}".format(item[0], item[1])
                uri = ''.join([i if i not in invalid_chars else '_' for i in uri])
                osn_terms.append("<{0}>".format(uri))

query = """
PREFIX skos:<http://www.w3.org/2004/02/skos/core#>
PREFIX rdf:<http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX rdfs:<http://www.w3.org/2000/01/rdf-schema#>
PREFIX xsd:<http://www.w3.org/2001/XMLSchema#>

SELECT ?osnConcept ?lgdoConcept
{
?osnConcept skos:exactMatch ?lgdoConcept .

FILTER (?osnConcept IN (""" + ", ".join(osn_terms) + """))
FILTER (STRSTARTS(STR(?lgdoConcept), "http://linkedgeodata.org/ontology"^^xsd:string))
}
"""

response = osn_graph.query(query)

valid_tags = []
lgd_concepts = []
for row in response:
    osn_concept = row[0]
    osn_concept = 'k:{0}'.format(osn_concept.split('k:')[-1])
    valid_tags.append(osn_concept)
    lgd_concepts.append(str(row[1]).split('/')[-1])

print('{0} valid tags: {1}\n\ncorresponding to the LGD concepts: {2}'.format(
        len(valid_tags), valid_tags, lgd_concepts))

#Exclude features that don't have the valid tags
to_drop = []
for tags, idx in zip(osm_features['tags'], osm_features.index):
    feature_tags = ['k:{0}/v:{1}'.format(item[0], item[1]) for item in tags.items()]
    if not any([tag in valid_tags for tag in feature_tags]):
        to_drop.append(idx)

print('{0} elements before cleaning'.format(len(osm_features)))
osm_features = osm_features.drop(to_drop)
print('{0} elements after cleaning'.format(len(osm_features)))

23 valid tags: ['k:highway/v:steps', 'k:highway/v:service', 'k:building/v:apartments', 'k:route/v:bicycle', 'k:natural/v:wood', 'k:power/v:substation', 'k:leisure/v:sports_centre', 'k:highway/v:unclassified', 'k:route/v:bus', 'k:highway/v:cycleway', 'k:highway/v:path', 'k:barrier/v:fence', 'k:waterway/v:stream', 'k:leisure/v:park', 'k:highway/v:residential', 'k:landuse/v:grass', 'k:place/v:suburb', 'k:amenity/v:parking', 'k:landuse/v:residential', 'k:highway/v:secondary', 'k:highway/v:footway', 'k:landuse/v:forest', 'k:natural/v:water']

corresponding to the LGD concepts: ['Steps', 'HighwayService', 'BuildingApartments', 'RouteBicycle', 'NaturalWood', 'Substation', 'SportsCentre', 'Unclassified', 'Bus', 'Cycleway', 'Path', 'Fence', 'Stream', 'Park', 'HighwayResidential', 'Grass', 'Suburb', 'Parking', 'LanduseResidential', 'Secondary', 'Footway', 'LanduseForest', 'NaturalWater']
124 elements before cleaning
93 elements after cleaning


Creating closed polygons with buffers:

In [13]:
linestring = "LINESTRING("

for i, point_data in enumerate(points_data):
    point = point_data.point
    linestring += str(point.longitude) + " " + str(point.latitude)
    if i < len(points_data)-1:
        linestring += ", "

linestring += ")"

trajectory = wkt.loads(linestring)

features = []
features_json = []
marker_data = []

to_drop = []
for item in osm_features.itertuples():
    try:
        feature0 = wkt.loads(item.geometry)
        json_feature0 = geojson.Feature(geometry=feature0, properties={"id": str(item.Index)})

        feature1 = feature0.buffer(buffer_size)
        json_feature1 = geojson.Feature(geometry=feature1)

        feature2 = polygonize_full(feature0)[0]
        json_feature2 = geojson.Feature(geometry=feature2)

        feature3 = cascaded_union([feature1, feature2])
        json_feature3 = geojson.Feature(geometry=feature3)

        #0: original geometry (linestring)
        #1: buffered 0 (polygon)
        #2: polygonized
        #3: union of 1 and 2
        # This is for visualization purposes.
        # A more efficient solution would be to buffer the polygonized line (feature2)
        features_json.append([json_feature0, json_feature1, json_feature2, json_feature3])
        features.append(feature3)

        rep_point = feature3.representative_point()
        popup_text = "{0}\n{1}".format(str(item.Index), repr(item.tags))
        if item.relation and len(item.relation) > 0:
            popup_text += " | part of: " + str(item.relation)
        marker_data.append(([rep_point.y, rep_point.x], popup_text))
    except Exception as e:
        #print(e)
        #print(item.Index)
        #print(item.label)
        #print(item.geometry)
        to_drop.append(item.Index)

osm_features = osm_features.drop(to_drop)

ParseException: Expected 'Z', 'M', 'ZM', 'EMPTY' or '(' but encountered : ')'


In [21]:
traj_map = folium.Map(tiles=tileset, attr=attribution, max_zoom=25)

for i, feat in enumerate(features_json):
    traj_map.choropleth(geo_data=feat[0], line_color='black', line_weight=3)
    #traj_map.choropleth(geo_str=feat[1], fill_color='gray', line_weight=1, fill_opacity=0.2)
    #traj_map.choropleth(geo_str=feat[2], fill_color='green', line_weight=1, fill_opacity=0.2)
    traj_map.choropleth(geo_data=feat[3], fill_color='red', line_weight=1, fill_opacity=.1)
    folium.Marker(location=marker_data[i][0], popup=marker_data[i][1]).add_to(traj_map)

start_mark.add_to(traj_map)
end_mark.add_to(traj_map)

line.add_to(traj_map)

traj_map.fit_bounds(line.get_bounds())

traj_map

Compute the intersections:

In [15]:
feature_intervals = osm.compute_intersections(gpx, osm_features) 
print("{0} intersections retrieved.".format(len(feature_intervals)))

150 intersections retrieved.


In [16]:
groups = feature_intervals.groupby(level=0)
print(len(groups), 'unique features.')

88 unique features.


Select OSM features based on parameters:

In [17]:
selected = []
for group in groups:
    if group[1]['length_ratio'].sum() > minimum_length_ratio or group[1]['duration_ratio'].sum() > minimum_duration_ratio:
        print('')
        print(group[0])
        print('relations:', osm_features.loc[group[0]]['relation'])
        print(osm_features.loc[group[0]]['label'], osm_features.loc[group[0]]['tags'])
        print("length ratio: {:.2f}%".format(group[1]['length_ratio'].sum()*100))
        print("duration ratio: {:.2f}%".format(group[1]['duration_ratio'].sum()*100))
        selected.append(group[0])


278498
relations: None
L'Isère {'boat': 'no', 'comment': 'Provenance du cadastre, les bords semblent correspondre au seuil maximal innondable', 'name': "L'Isère", 'natural': 'water', 'note': 'taggé en mode « new tagging » cf wiki', 'source': 'cadastre-dgi-fr source : Direction Générale des Impôts - Cadastre;mise à jour : 2009', 'type': 'multipolygon', 'water': 'river'}
length ratio: 34.29%
duration ratio: 34.83%

2808054
relations: None
Rive Gauche de l'Isère, amont de Grenoble {'name': "Rive Gauche de l'Isère, amont de Grenoble", 'network': 'rcn', 'route': 'bicycle', 'type': 'route'}
length ratio: 39.12%
duration ratio: 40.76%

3922430
relations: None
13 : Poisat => Meylan {'colour': '#28b3b4', 'from': 'Poisat - Prémol', 'name': '13 : Poisat => Meylan', 'network': 'TAG', 'opening_hours': 'Mo-Sa 05:30-20:30; Su 06:30-20:30', 'operator': 'Semitag Eybens', 'public_transport:version': '2', 'ref': '13', 'route': 'bus', 'to': 'Meylan - Lycée du Grésivaudan', 'type': 'route', 'wheelchair': 

In [18]:
selected_map = folium.Map(tiles=tileset, attr=attribution, max_zoom=25)

for osm_index in selected:
    index = osm_features.index.get_loc(osm_index)
    selected_map.choropleth(geo_data=features_json[index][3], line_weight=4, 
                            line_opacity=.6, line_color='black', fill_color='red', fill_opacity=.1)
    #folium.Marker(location=marker_data[index][0], popup=marker_data[index][1]).add_to(selected_map)
    
start_mark.add_to(selected_map)
end_mark.add_to(selected_map)
line.add_to(selected_map)

selected_map.fit_bounds(line._get_self_bounds())

selected_map

In [19]:
#end